In [17]:
import numpy as np
import matplotlib.pyplot as plt
import scipy
import sympy as sp
from sympy.vector import CoordSys3D

from matplotlib import animation, rc
from IPython.display import HTML, display
rc('animation', html='jshtml')
import seaborn as sns
C = CoordSys3D('')

#Define plotting style:
sns.set() #Set style
sns.set_style('ticks',{'font.family':'serif', 'font.serif':'Times New Roman'})
sns.set_context('poster', font_scale=0.8,  rc={"lines.linewidth": 5})

## Problema 1 (Air Hockey)

<font size=3px>Um disco de massa $m = 200$ g está em repouso no centro de uma mesa quadrada de air hockey de lado $l = 2$ m. O disco é atingido por uma raquete na direção de $\theta = 30^{\circ}$ com a horizontal. Se o tempo de contato entre a raquete e o disco é de $\Delta t = 0,1$ s e a força exercida durante o contato foi de 1 N, determine a trajetória do disco:<br>
    a) Durante o contato com a raquete<br>
    b) Após o contato<br>
    c) Em que instante o disco atingirá uma das laterais da mesa?
</font>

In [45]:
#Definir variaveis/parametros:
m,l,tt,t,dt,g,F = sp.symbols('m,l,theta,t,Δt,g,F',positive=True)
subsList = [(m,0.2),(l,2.),(tt,np.pi/6),(dt,0.1),(F,1.)]

In [63]:
#item a)
#Durante o contato:
r0 = 0*C.i
v0 = 0*C.i
Fv = F*sp.cos(tt)*C.i + F*sp.sin(tt)*C.j
a = Fv/m
r = lambda t: r0 + v0*t + (a/2)*t**2
v = sp.diff(r(t),t)
resp = display(r(t))
r(t).subs(subsList).evalf(4)

(F*t**2*cos(theta)/(2*m))*.i + (F*t**2*sin(theta)/(2*m))*.j

2.165*t**2*.i + 1.25*t**2*.j

In [64]:
#item b)
#Após o contato F = 0, a = 0
t0 = dt
r0 = r(dt)
v0 = v.subs(t,dt)
r2 = lambda t: r0 + v0*(t-t0)
resp = display(sp.simplify(r2(t)))
r2num = r2(t).subs(subsList).evalf(4)
r2num

(F*Δt*(2*t - Δt)*cos(theta)/(2*m))*.i + (F*Δt*(2*t - Δt)*sin(theta)/(2*m))*.j

(0.433*t - 0.02165)*.i + (0.25*t - 0.0125)*.j

In [68]:
#item c)
#O disco atingirá uma das laterais quando x(t) = +-1 ou y(t) = +-1
#Do resultado anterior temos que x > -1 e y > -1.
#Logo buscamos o menor tempo entre as soluções x = 1 e y = 1:
t1sol = sp.solve(sp.Eq(r2num.dot(C.i),1),t)[0]
t2sol = sp.solve(sp.Eq(r2num.dot(C.j),1),t)[0]
tsol = min(t1sol,t2sol)
print(t1sol,t2sol)
print('menor tempo = ',tsol)

2.35946882217090 4.05000000000000
menor tempo =  2.35946882217090


In [84]:
t0  = 0.
tC = 0.1
v0x, v0y = 0.,0.
x0,y0 = 1.,1.
a = 1./0.2
theta = 30.*np.pi/180.
l = 2.

ax = a*np.cos(theta)
ay = a*np.sin(theta)
v1x = v0x + ax*tC
v1y = v0y + ay*tC
x1 = x0 + v0x*tC + (ax*tC**2)/2.
y1 = y0 + v0y*tC + (ay*tC**2)/2.
xF = lambda t: x0 + v0x*t + (ax*t**2)/2. if t <= tC else x1 + v1x*(t-tC)
yF = lambda t: y0 + v0y*t + (ay*t**2)/2. if t <= tC else y1 + v1y*(t-tC)

# print('ax = %1.2f m/s^2, ay = %1.2f m/s^2, v1x = %1.2f m/s, v1y = %1.2f m/s, x1 = %1.2f m, y1 = %1.2f m' %(ax,ay,v1x,v1y,x1,y1))

tmin, tmax = 0.,float(tsol)
dt = 0.05
tpts = np.linspace(tmin,tmax,100)

fig = plt.figure(figsize=(30,10))
ax1 = plt.subplot(131)
ax1.plot([0.,l,l,0.,0.],[0.,0.,l,l,0.],'-')
pt, = ax1.plot([xF(tmin)],[yF(tmin)],'o',markersize=15)
line1, = ax1.plot([xF(tmin)],[yF(tmin)],'--',linewidth=3)
vec = ax1.quiver([xF(tmin)],[yF(tmin)],[np.cos(theta)],[np.sin(theta)],scale=5.5,alpha = 0.2)
xlabel = ax1.set_xlabel('x (m)')
ylabel = ax1.set_ylabel('y (m)')

ax2 = plt.subplot(132)
xLine, = ax2.plot([tmin],[xF(tmin)],linewidth=4,color='r')
xlabel = ax2.set_xlabel('t (s)')
ylabel = ax2.set_ylabel('x (m)')
ax2.set_xlim(tmin,2*tC)
ax2.set_ylim(xF(tmin),xF(2*tC))

ax3 = plt.subplot(133)
yLine, = ax3.plot([tmin],[yF(tmin)],linewidth=4,color='g')
xlabel = ax3.set_xlabel('t (s)')
ylabel = ax3.set_ylabel('y (m)')
ax3.set_xlim(tmin,2*tC)
ax3.set_ylim(yF(tmin),yF(2*tC))

text = ax1.text(0.1,0.1,r't = %1.2f s' %tmin)
# plt.tight_layout(pad=0.4, w_pad=0.5, h_pad=1.0)
# plt.tight_layout()


def init():
    line1.set_data([xF(tmin)],[yF(tmin)])
    pt.set_data([xF(tmin)],[yF(tmin)])
    vec.set_offsets([xF(tmin),yF(tmin)])
    xLine.set_data([tmin],[xF(tmin)])
    yLine.set_data([tmin],[yF(tmin)])    
    text.set_text(r't = %1.2f s' %tmin)
    return (pt,line1,vec,xLine,yLine,text)
def animate(i):
    tA = tmin+i*dt
    newpts = np.linspace(tmin,tA,100)
    xPts = [xF(t) for t in newpts]
    yPts = [yF(t) for t in newpts]
    xpt,ypt = xF(newpts[-1]),yF(newpts[-1])
    pt.set_data([xpt],[ypt])
    line1.set_data(xPts,yPts)
    vec.set_offsets([xpt,ypt])
    xLine.set_data(newpts,xPts)
    yLine.set_data(newpts,yPts)    
    
    text.set_text(r't = %1.2f s' %tA)    
    if tA > tC:
        vec.set_offsets([2*l,2*l])
        
    return (pt,line1,vec,xLine,yLine,text)


anim = animation.FuncAnimation(fig, animate, init_func=init,
                               frames=int((tmax-tmin)/dt), interval=200, 
                               blit=True)
anim.save('airHockey.mp4', fps=15, extra_args=['-vcodec', 'libx264'])
plt.close()
anim
# plt.show()

## Problema 2 (Máquina de Atwood)

<font size=3px>Dois blocos de massa $M_1$ e $M_2$ estão presos a uma roldana por um fio ideal, conforme mostra a figura. Se o sistema parte do repouso, determine quanto tempo o bloco mais leve ($M_1$) leva para subir uma altura $h$<br>
</font>
<img src="atwood.png" alt="Drawing" style="width: 200px;"/>

In [86]:
#Definir variaveis/parametros:
m1,m2,h,t,g,T,a = sp.symbols('M_1,M_2,h,t,g,T,a',positive=True)

In [89]:
#Forças
T1 = T*C.j
T2 = T*C.j
F1 = -m1*g*C.j + T1
F2 = -m2*g*C.j + T2

In [90]:
#Aceleração (as acelerações em módulo são iguais)
a1 = a*C.j
a2 = -a*C.j
#Segunda Lei:
resp = display(sp.Eq(F1,m1*a1))
resp = display(sp.Eq(F2,m2*a2))

Eq((-M_1*g + T)*.j, M_1*a*.j)

Eq((-M_2*g + T)*.j, (-M_2*a)*.j)

In [97]:
#Solução para a aceleração
sol = sp.solve([sp.Eq(F1,m1*a1),sp.Eq(F2,m2*a2)],(a,T))
asol = sol[a]
asol

(-M_1*g + M_2*g)/(M_1 + M_2)

In [98]:
#Trajetória M1:
r0 = 0*C.j
v0 = 0*C.j
r = lambda t: r0 + v0*t + asol*C.j*(t**2)/2
r(t)

(t**2*(-M_1*g + M_2*g)/(2*(M_1 + M_2)))*.j

In [102]:
#M1 atinge h quando:
tsol = sp.solve(sp.Eq(r(t).dot(C.j),h),t)[1]
sp.simplify(tsol)

sqrt(2)*sqrt(h)*sqrt(-1/(M_1 - M_2))*sqrt(M_1 + M_2)/sqrt(g)

## Problema 3 (Força de Atrito)

<font size=3px>Dois blocos de massa $M_1$ e $M_2$ estão um sobre o outro e deslizam em um plano inclinado, conforme mostra a figura. O coeficiente de atrito estático entre o bloco e o plano é $\mu_s = 0,4$ e o coeficiente de atrito cinético é $\mu_k = 0,2$.<br>
(a) Faça um diagrama de forças para cada bloco. <br>
(b) Determine o ângulo máximo para que o sistema esteja em equilíbrio.<br>
(c) Se $\theta = 60^\circ$ e os blocos deslizam juntos (mesma aceleração), determine a aceleração do sistema.<br>
(d) Para a situação do item acima, determine o módulo da força de atrito entre os blocos, se $M_1 = 2$ kg.
</font>
<img src="blocksPlane2.jpg" alt="Drawing" style="width: 300px;"/>

In [120]:
#Definir variaveis/parametros:
m1,m2,g,tt,a,muk,mus,NA,NB,FA,FB = sp.symbols('M_1,M_2,g,theta,a,mu_k,mu_s,N_A,N_B,FA,FB',positive=True)
subsList = [(m1,2.),(g,9.8),(tt,np.pi/3),(mus,0.4),(muk,0.2)]

In [105]:
#item a)
#Forças (adotando um sistema paralelo ao plano inclinado)
#Forças em A:
NAv = NA*C.j #normal entre A-B
FatAv = FA*C.i #atrito entre A-B
PAv = -m1*g*sp.sin(tt)*C.i-m1*g*sp.cos(tt)*C.j #força peso de A
#Forças em B
NARv = -NAv #reação da normal entre A-B
FatRAv = -FatAv #reação do atrito entre A-B
PBv = -m2*g*sp.sin(tt)*C.i-m2*g*sp.cos(tt)*C.j #força peso de B
NBv = NB*C.j #normal entre B e plano
FatBv = FB*C.i #atrito entre B e plano


In [107]:
#item b)
#Força resultante em A:
FRA = NAv+FatAv+PAv
resp = display(FRA)
#Força resultante em B:
FRB = NARv+FatRAv+PBv+NBv+FatBv
resp = display(FRB)

(FA - M_1*g*sin(theta))*.i + (-M_1*g*cos(theta) + N_A)*.j

(-FA + FB - M_2*g*sin(theta))*.i + (-M_2*g*cos(theta) - N_A + N_B)*.j

In [112]:
#Solução para equilíbrio (FRA = 0, FRB = 0)
sols = sp.solve([sp.Eq(FRA.dot(C.i),0),sp.Eq(FRA.dot(C.j),0),sp.Eq(FRB.dot(C.i),0),sp.Eq(FRB.dot(C.j),0)],(NA,NB,FA,FB))
NAsol = sols[NA]
NBsol = sols[NB]
FAsol = sols[FA]
FBsol = sols[FB]
print("NA:")
resp = display(NAsol)
print("NB:")
resp = display(NBsol)
print("FA:")
resp = display(FAsol)
print("FB:")
resp = display(FBsol)

NA:


M_1*g*cos(theta)

NB:


M_1*g*cos(theta) + M_2*g*cos(theta)

FA:


M_1*g*sin(theta)

FB:


M_1*g*sin(theta) + M_2*g*sin(theta)

In [121]:
#O angulo maximo será quando FB = mus*NB
mussol = sp.solve(sp.Eq(FBsol,mus*NBsol),mus)[0]
resp = display(sp.Eq(mus,mussol))
thetasol = sp.solve(sp.Eq(FBsol,mus*NBsol),tt)[0]
print(thetasol.subs(subsList).evalf())

Eq(mu_s, tan(theta))

0.380506377112366


In [129]:
#item c)
#Se a acelaração é a mesma, devemos ter FRA = m1*a, FRB=m2*a.
#Além disso, como o atrito é cinético:
FatBv = NB*muk*C.i #atrito entre B e plano
FRB = NARv+FatRAv+PBv+NBv+FatBv
sols = sp.solve([sp.Eq(FRA.dot(C.i),-m1*a),sp.Eq(FRA.dot(C.j),0),sp.Eq(FRB.dot(C.i),-m2*a),sp.Eq(FRB.dot(C.j),0)],(NA,NB,FA,a))
NAsol = sols[NA]
NBsol = sols[NB]
FAsol = sols[FA]
asol = sols[a]
print("NA:")
resp = display(NAsol)
print("NB:")
resp = display(NBsol)
print("FA:")
resp = display(FAsol)
print("a:")
resp = display(asol)
print('a = ',asol.subs(subsList).evalf(3),'m/s^2')
print('FA = ',FAsol.subs(subsList).evalf(3),'N')

NA:


M_1*g*cos(theta)

NB:


M_1*g*cos(theta) + M_2*g*cos(theta)

FA:


M_1*g*mu_k*cos(theta)

a:


-g*mu_k*cos(theta) + g*sin(theta)

a =  7.51 m/s^2
FA =  1.96 N


## Problema 4 (Tensão)

<font size=3px>Dado o sistema abaixo, determine:<br>
(a) o diagrama de forças para cada bloco <br>
(b) o valor de $m_B$ (em função de $m_A,\theta_1,\theta_2$) para que o sistema fique em equilíbrio.
</font>
<img src="blocksPlane.jpg" alt="Drawing" style="width: 300px;"/>

## Problema 5 (Movimento Circular)

<font size=3px>Um corpo pequeno de massa m está suspenso por um fio de comprimento $L$.<br>
O corpo gira em um círculo horizontal de raio $r$ com velocidade constante $v$, como mostrado na figura.
Encontrar:<br>
(a) a velocidade do corpo <br>
(b) o período de revolução (1 volta)
</font>
<img src="penduloConico.png" alt="Drawing" style="width: 300px;"/>

### Problema 6 (Movimento Circular)

<font size=3px>Um carro de $1800$ kg passa sobre uma lombada na rua que segue o arco de uma circunferência de raio $20,4$ m como se mostra na figura.<br>
    (a) Qual é a força que a rua exerce sobre o carro quando ele passa pelo ponto mais alto da lombada a
        uma velocidade de $30$ km/h?<br>
    (b) Qual é a máxima velocidade que o carro pode ter passando pelo ponto mais alto da
lombada sem perder contato com a rua?
</font>

### Problema 7 (Movimento Circular e Atrito)

<font size=3px>Uma moeda de massa $3,1$ g fica sobre um pequeno bloco de $20$ g, que por sua vez, descansa sobre um disco giratório. Os coeficientes de atrito entre o bloco e o disco são: $0,75$ (estático) e $0,64$ (cinético). Entre a moeda e o bloco os coeficientes de atrito são: $0,52$ (estático) e $0,45$ (cinético).
Qual seria a máxima taxa de rotação (em revoluções por minuto) que o disco pode ter sem que o bloco ou a moeda escorreguem encima do disco?
</font>
<img src="movimentoCircularAtrito.png" alt="Drawing" style="width: 300px;"/>